<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Redo-the-experiment-of-Christof-Monz-in-Numpy" data-toc-modified-id="Redo-the-experiment-of-Christof-Monz-in-Numpy-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Redo the experiment of Christof Monz in Numpy</a></span><ul class="toc-item"><li><span><a href="#Two-experiments" data-toc-modified-id="Two-experiments-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Two experiments</a></span></li><li><span><a href="#The-task" data-toc-modified-id="The-task-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>The task</a></span></li><li><span><a href="#Redo-Monz-experiment-in-Numpy" data-toc-modified-id="Redo-Monz-experiment-in-Numpy-1.3"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>Redo Monz experiment in Numpy</a></span><ul class="toc-item"><li><span><a href="#Outcome" data-toc-modified-id="Outcome-1.3.1"><span class="toc-item-num">1.3.1&nbsp;&nbsp;</span>Outcome</a></span></li></ul></li><li><span><a href="#Double-for-loop-:-over-the-elements-individually" data-toc-modified-id="Double-for-loop-:-over-the-elements-individually-1.4"><span class="toc-item-num">1.4&nbsp;&nbsp;</span>Double for loop : over the elements individually</a></span><ul class="toc-item"><li><span><a href="#Outcome" data-toc-modified-id="Outcome-1.4.1"><span class="toc-item-num">1.4.1&nbsp;&nbsp;</span>Outcome</a></span></li></ul></li></ul></li><li><span><a href="#Original-code-of-Monz" data-toc-modified-id="Original-code-of-Monz-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Original code of Monz</a></span></li></ul></div>

# Redo the experiment of Christof Monz in Numpy

The message **never use a loop**, but use *vectorized computations* holds just as well for computing in `numpy` or `pandas` as for `pytorch` or `tensorflow`.

So we repeat the experiment here in numpy. The technique we use to filter (_sample_) the large 2D matrix is called [fancy indexing](https://jakevdp.github.io/PythonDataScienceHandbook/02.07-fancy-indexing.html) and is really worthwhile studying. It works very  fast, and does in effect do the same job as the view described in the code of Monz.

## Two experiments

We do not "feel" the bad effects of _for looping_ when we exactly repeat Christofs (sampling over rows) experiment. But if we also loop over the columns, with the same step size, we really do see the difference between the "for" and the "best" run.

Times are measured on a Macbook Pro (2015)  with 2.9 GHz Intel Core i5 processor and 16 GB  RAM.

In [2]:
import numpy as np
import time

# global variables
input_size = 2000
hidden_size = 4096


##  two np matrices of shape (2000, 4096)

A= np.random.rand(input_size,hidden_size)
B=  np.random.rand(input_size,hidden_size)
A.shape

(2000, 4096)

## The task

Compute the element wise product of two 2D matrices.

In [3]:
%%time


C= A*B

print(C.shape)

(2000, 4096)
CPU times: user 26.7 ms, sys: 22.9 ms, total: 49.6 ms
Wall time: 47.7 ms


## Redo Monz experiment in Numpy

We do each method with three stepsizes and report the stepsize, the method name, the time, and the start of the output. 

Note that the step size was fixed to 100 in Cristofs experiment. We add stepsizes of 10 and 1 (1 is of course the complete matrix).
### Outcome

The `for` method beats the `best` method consistently, however they are in the same order of magnitude.
The other methods perform more or less similar to computing the complete product (`nofilter`).
When the stepsize equals 1 (so we compute the complete product) all methods time in the same order of magnitude.

In [4]:
%%time 

def experiment(x,y,method='best',step_size=100, max_input = int(1e6)):
    repeats = max_input//input_size
    #print('start')
    start_time = time.time()
    for i in range(1,repeats+1):
        if i%1000 == 0:
            print(i)
        if method=='nofilter':    # no filter at all
            output= x*y    
        elif method=='for':   # for loop
            output_index = 0
            output=np.zeros((input_size//step_size,hidden_size))
            for j in range(step_size-1,input_size,step_size):
                output[output_index] = x[j] * y[j]
                output_index += 1
        elif method == 'allthenfor': # first product, then filter by a for loop
            z = x*y
            output_index = 0
            output=np.zeros((input_size//step_size,hidden_size))
            for j in range(step_size-1,input_size,step_size):
                output[output_index] = z[j]
                output_index += 1
        elif method == 'better':  # fancy indexing after the product
            output = (x*y)[range(step_size-1,input_size,step_size),:]
        elif method == 'best':  # fancy indexing before the product
            output = (x[range(step_size-1,input_size,step_size),:]*
                      y[range(step_size-1,input_size,step_size),:])
    elapsed_time = time.time() - start_time    
    return elapsed_time,output

'''
for method in ['nofilter','allthenfor','for','better','best']:
    step_size=100
    tijd,out= experiment(A,B,method=method,step_size=step_size)
    print(step_size,method,tijd,out[0,:5])
'''

for step_size in [100,10,1]:
    for method in ['nofilter','allthenfor','for','better','best']:
        tijd,out= experiment(A,B,method=method,step_size=step_size)
        print(step_size,method,tijd,out[0,:5])    

100 nofilter 16.126432180404663 [0.50812953 0.23894935 0.23581109 0.1770699  0.37806036]
100 allthenfor 14.560197114944458 [0.50264173 0.84403391 0.31848951 0.25569864 0.63406363]
100 for 0.08021712303161621 [0.50264173 0.84403391 0.31848951 0.25569864 0.63406363]
100 better 14.425140142440796 [0.50264173 0.84403391 0.31848951 0.25569864 0.63406363]
100 best 0.11473417282104492 [0.50264173 0.84403391 0.31848951 0.25569864 0.63406363]
10 nofilter 14.875795125961304 [0.50812953 0.23894935 0.23581109 0.1770699  0.37806036]
10 allthenfor 18.194615125656128 [0.20850192 0.15585488 0.09869398 0.23816242 0.13696984]
10 for 1.2545669078826904 [0.20850192 0.15585488 0.09869398 0.23816242 0.13696984]
10 better 15.554318904876709 [0.20850192 0.15585488 0.09869398 0.23816242 0.13696984]
10 best 2.2483460903167725 [0.20850192 0.15585488 0.09869398 0.23816242 0.13696984]
1 nofilter 13.711044073104858 [0.50812953 0.23894935 0.23581109 0.1770699  0.37806036]
1 allthenfor 27.244115114212036 [0.50812953 

##  Double for loop : over the elements individually

We do a double for loop, over the columns and the rows.

We restrict to the for and best runs.

We change the hidden size to 4100, so it is divisible by 10 and 100. 

Note that we let the expeirment run here by default only 100K times. The double for loop amounts to 16M computations in the for loop, so that takes a lot of time.....

### Outcome

`best` is always an order of maginitude faster than `for`.

In [5]:
%%time 
## double for loop : over the elements individually

input_size = 2000
hidden_size = 4100

A= np.random.rand(input_size,hidden_size)
B=  np.random.rand(input_size,hidden_size)


def experiment(x,y,method='best',step_size=100, max_input = int(1e5)):
    repeats = max_input//input_size
    #print('start')
    start_time = time.time()
    for i in range(1,repeats+1):
        if i%1000 == 0:
            print(i)
        if method=='nofilter':    # no filter at all
            output= x*y    
        elif method=='for':   # for loop
            output=np.zeros((input_size//step_size,hidden_size//step_size))
            output_index_j = 0
            for j in range(step_size-1,input_size,step_size):  # j is row
                output_index_i = 0
                for i in range(step_size-1,hidden_size,step_size):  # i is column
                    output[output_index_j,output_index_i] = x[j,i] * y[j,i]
                    output_index_i += 1
                output_index_j += 1
        elif method == 'allthenfor': # first product, then filter by a for loop
            z = x*y
            output_index = 0
            output=np.zeros((input_size//step_size,hidden_size))
            for j in range(step_size-1,input_size,step_size):
                output[output_index] = z[j]
                output_index += 1
        elif method == 'better':  # fancy indexing after the product
            output = (x*y)[range(step_size-1,input_size,step_size),:]
        elif method == 'best':  # fancy indexing before the product
            row = np.arange(step_size-1,input_size,step_size)
            col= np.arange(step_size-1,hidden_size,step_size)
            smallx= x[row[:, np.newaxis], col]
            smally=y[row[:, np.newaxis], col]
            output =  smallx * smally
    elapsed_time = time.time() - start_time    
    return elapsed_time,output

for step_size in [100,10,1]:
    for method in ['best','for']:
        tijd,out= experiment(A,B,method=method,step_size=step_size)
        print(step_size,method,tijd,out.shape,out[0,:5])  

100 best 0.001085042953491211 (20, 41) [0.56075119 0.09664409 0.17087498 0.44948774 0.1755863 ]
100 for 0.022330760955810547 (20, 41) [0.56075119 0.09664409 0.17087498 0.44948774 0.1755863 ]
10 best 0.0838780403137207 (200, 410) [0.22263665 0.03570748 0.04859623 0.65376252 0.24604552]
10 for 2.1343231201171875 (200, 410) [0.22263665 0.03570748 0.04859623 0.65376252 0.24604552]
1 best 6.50712776184082 (2000, 4100) [0.29378663 0.60332941 0.42967505 0.65462595 0.65623145]
1 for 216.48570704460144 (2000, 4100) [0.29378663 0.60332941 0.42967505 0.65462595 0.65623145]
CPU times: user 3min 43s, sys: 2.1 s, total: 3min 45s
Wall time: 3min 45s


# Original code of Monz

```
import torch
import sys
import torch.nn as nn
import time

torch.manual_seed(1)

# grun-pascal python ~/code/pytorch/toy/soos.py
# srun --unbuffered --partition=gpu --gres=gpu:1 --mem=40G --nodelist=ilps-gpu10 python ~/code/pytorch/toy/soos.py for

input_size = 2000
hidden_size = 4096
step_size = 100

# method = 'for'
method = sys.argv[1]

if method == 'bestest':
    input_size *= step_size

x = torch.rand([input_size,hidden_size]).cuda()
y = torch.rand([input_size,hidden_size]).cuda()


output_size = input_size//step_size
output = torch.zeros([output_size,hidden_size]).cuda()


max_input = int(1e10)
repeats = max_input//input_size

start_time = time.time()

print('start')
for i in range(1,repeats+1):
    if i%5000 == 0:
        print(i)

    if method == 'for':
        output_index = 0
        for j in range(step_size-1,input_size,step_size):
            output[output_index] = x[j] * y[j]
            output_index += 1
    elif method == 'allthenfor':
        z = x*y
        output_index = 0
        for j in range(step_size-1,input_size,step_size):
            output[output_index] = z[j]
            output_index += 1
    elif method == 'better':
        output = (x*y).view(output_size,-1)[:,(step_size-1)*hidden_size:step_size*hidden_size].contiguous()
    elif method == 'best' or method == 'bestest':
        output = (x.view(output_size,-1)[:,(step_size-1)*hidden_size:step_size*hidden_size] \
                * y.view(output_size,-1)[:,(step_size-1)*hidden_size:step_size*hidden_size]).contiguous()

    if i==repeats:
        # print(output.size())
        print(output[3,0:5])

elapsed_time = time.time() - start_time
print(time.strftime("%H:%M:%S", time.gmtime(elapsed_time)))
outputs_per_sec = int(((max_input/step_size)/elapsed_time)/1000)
print("outputs per sec = " +  "{:,}".format(outputs_per_sec) + " K")

sys.exit()
```